This notebook contains a finite element analysis of a surface wave problem. 

In [1]:
import netgen.gui 
from ngsolve import *
import netgen.geom2d as geom2d

optfile ./ng.opt does not exist - using default values
togl-version : 2
OCC module loaded
loading ngsolve library
NGSolve-6.2.2403
Using Lapack
Including sparse direct solver UMFPACK
Running parallel using 4 thread(s)


The next step involves setting up of the working domain along with perfectly matched layers (PMLs). 
The domain is rectangular in shape with PML on three of its sides and free surface at $y=0$. 

In [2]:
geo = geom2d.SplineGeometry()
p1,p2,p3,p4,p5,p6,p7,p8 = [geo.AppendPoint(x,y) for x,y in [(-2.5,-2.5),(2.5,-2.5),(2.5,0),(2,0),(2,-2),(-2,-2),(-2,0),(-2.5,0)] ]
origin = geo.AppendPoint(0,0)

geo.Append (["line", p4, origin],bc="bc1",leftdomain=1,rightdomain=0)
geo.Append (["line", origin, p7],bc="bc2",leftdomain=1,rightdomain=0)

geo.Append (["line", p1, p2],leftdomain=2,rightdomain=0)
geo.Append (["line", p2, p3],leftdomain=2,rightdomain=0)
geo.Append (["line", p3, p4],leftdomain=2,rightdomain=0)
geo.Append (["line", p4, p5],leftdomain=2,rightdomain=1)
geo.Append (["line", p5, p6],leftdomain=2,rightdomain=1)
geo.Append (["line", p6, p7],leftdomain=2,rightdomain=1)
geo.Append (["line", p7, p8],leftdomain=2,rightdomain=0)
geo.Append (["line", p8, p1],leftdomain=2,rightdomain=0)

geo.SetMaterial(1, "inner")
geo.SetMaterial(2, "pmlregion")

mesh=Mesh(geo.GenerateMesh (maxh=0.1))
mesh.SetPML(pml.Cartesian((-2,-2),(-2,0),1j),"pmlregion")
Draw(mesh)


 Generate Mesh from spline geometry


In [3]:
mu = 0.1
muA = 0.01
muB = 0.02
rho = 1
rhoA = 2
rhoB = 1.1
kA = 1
gammaA = 1
omega = sqrt((mu*gammaA+muA*kA**2)/rhoA)
u0 = 1;

In [4]:
fes = H1(mesh, order=3, complex=True)
u, v = fes.TnT()

f = -u0*exp(gammaA*y-1j*kA*x)*(rho*omega**2+mu*gammaA**2-mu*kA**2);
f1 = u0*exp(-1j*kA*x)*(gammaA*mu+kA**2*muB-rhoB*omega**2);

force = 1j*kA*(muA-muB)

In [5]:
a = BilinearForm(fes)
a += mu*grad(u)*grad(u)*dx+rho*omega**2*u*v*dx
a += -rhoA*omega**2*u*v*ds+muA*grad(u).Trace()*grad(v).Trace()*ds("bc1")
a += -rhoB*omega**2*u*v*ds+muB*grad(u).Trace()*grad(v).Trace()*ds("bc2")

b = LinearForm(fes)
b += -f*v*dx;
b += -f1*v*ds("bc2")
#b += force[1]*v*ds

In [6]:
a.Assemble()
b.Assemble()

gfu = GridFunction(fes, name="u")
gfu.vec.data = a.mat.Inverse() * b.vec


In [7]:
Draw(gfu)